In [2]:
from sec_edgar_api import EdgarClient

In [3]:
edgar = EdgarClient(user_agent="<Sample Company Name> <Admin Contact>@<Sample Company Domain>")
edgar

In [9]:
edgar.get_submissions(cik="320193")

{'cik': '320193',
 'entityType': 'operating',
 'sic': '3571',
 'sicDescription': 'Electronic Computers',
 'insiderTransactionForOwnerExists': 0,
 'insiderTransactionForIssuerExists': 1,
 'name': 'Apple Inc.',
 'tickers': ['AAPL'],
 'exchanges': ['Nasdaq'],
 'ein': '942404110',
 'description': '',
 'website': '',
 'investorWebsite': '',
 'category': 'Large accelerated filer',
 'fiscalYearEnd': '0930',
 'stateOfIncorporation': 'CA',
 'stateOfIncorporationDescription': 'CA',
 'addresses': {'mailing': {'street1': 'ONE APPLE PARK WAY',
   'street2': None,
   'city': 'CUPERTINO',
   'stateOrCountry': 'CA',
   'zipCode': '95014',
   'stateOrCountryDescription': 'CA'},
  'business': {'street1': 'ONE APPLE PARK WAY',
   'street2': None,
   'city': 'CUPERTINO',
   'stateOrCountry': 'CA',
   'zipCode': '95014',
   'stateOrCountryDescription': 'CA'}},
 'phone': '(408) 996-1010',
 'flags': '',
 'formerNames': [{'name': 'APPLE INC',
   'from': '2007-01-10T00:00:00.000Z',
   'to': '2019-08-05T00:00:0

In [7]:
edgar.get_company_facts(cik="789019")

{'cik': 789019,
 'entityName': 'Microsoft Corporation',
 'facts': {'dei': {'EntityCommonStockSharesOutstanding': {'label': 'Entity Common Stock, Shares Outstanding',
    'description': "Indicate number of shares or other units outstanding of each of registrant's classes of capital or common stock or other ownership interests, if and as stated on cover of related periodic report. Where multiple classes or units exist define each class/interest by adding class of stock items such as Common Class A [Member], Common Class B [Member] or Partnership Interest [Member] onto the Instrument [Domain] of the Entity Listings, Instrument.",
    'units': {'shares': [{'end': '2009-10-19',
       'val': 8879121378,
       'accn': '0001193125-09-212454',
       'fy': 2010,
       'fp': 'Q1',
       'form': '10-Q',
       'filed': '2009-10-23',
       'frame': 'CY2009Q3I'},
      {'end': '2010-01-25',
       'val': 8770460922,
       'accn': '0001193125-10-015598',
       'fy': 2010,
       'fp': 'Q2',
 

# Use sec-edgar-downloader

In [8]:
from sec_edgar_downloader import Downloader

dl = Downloader()

dl.get("10-Q", "0000789019")

Skipping filing detail download for '0001032210-01-000273' due to network error: 404 Client Error: Not Found for url: https://www.sec.gov/Archives/edgar/data/789019/000103221001000273/0001.txt.
Skipping filing detail download for '0001032210-00-500038' due to network error: 404 Client Error: Not Found for url: https://www.sec.gov/Archives/edgar/data/789019/000103221000500038/0001.txt.


69

# Parse and Extract from .HTML

In [91]:
from bs4 import BeautifulSoup
import pandas as pd

# <table>, <tr>, <td>, and <th>: These tags are used to create tables. 
# <table> is for the table itself,
# <tr> defines a row,
# <td> defines a cell, and 
# <th> defines a header cell.

In [114]:
with open(r'sec-edgar-filings\0000320193\10-Q\0000320193-20-000010\filing-details.html', 'r') as f:
    contents = f.read()
soup = BeautifulSoup(contents, 'xml')

In [133]:
all_tables = soup.find_all('table')

In [160]:
data = [] # row x col [[1,2,3,4,5], [1,2,3,4,5], [1,2,3,4,5]] = 3 rows, 5 columns

# Loop over each row
for row in all_tables[12].find_all('tr')[:]: #
    # print(f'row: {row}')
    cols = []
    # Loop over each cell in the row
    for cell in row.find_all(['td', 'th'])[:]:
        # print(cell)
        # Get the colspan and rowspan attributes, defaulting to 1 if they don't exist
        colspan = int(cell.get('colspan', 1))
        rowspan = int(cell.get('rowspan', 1))

        # print(f'cell: {cell.text.strip()}\ncolspan: {colspan}\nrowspan: {rowspan}')
        # If the cell spans multiple rows or columns, add copies of it to the cols list
        for i in range(rowspan):
            for j in range(colspan):
                cols.append(cell.text.strip())


    # Add the cols list to the data list
    data.append(cols)
    # print(data)


# # Create a pandas DataFrame from the data
df = pd.DataFrame(data)
df.columns = pd.MultiIndex.from_arrays([df.iloc[2].values, df.iloc[3].values])
df = df.iloc[4:]
df

Three Months Ended  \
                                                  December 28, 2019   
4                                     Net sales:                      
5                                       Products                  $   
6                                       Services             12,715   
7                                Total net sales             91,819   
8                                                                     
9                                 Cost of sales:                      
10                                      Products             52,075   
11                                      Services              4,527   
12                           Total cost of sales             56,602   
13                                  Gross margin             35,217   
14                                                                    
15                           Operating expenses:                      
16                      Research and development              4,451   
17           Selling, general and administrative              5,197   
18                      Total operating expenses              9,648   
19                                                                    
20                              Operating income             25,569   
21                   Other income/(expense), net                349   
22      Income before provision for income taxes             25,918   
23                    Provision for income taxes              3,682   
24                                    Net income                  $   
25                                                                    
26                           Earnings per share:                      
27                                         Basic                  $   
28                                       Diluted                  $   
29                                                                    
30  Shares used in computing earnings per share:                      
31                                         Basic          4,415,040   
32                                       Diluted          4,454,604   

                                                                              \
   December 28, 2019 December 28, 2019   December 29, 2018 December 29, 2018   
4                                                                              
5             79,104                                     $            73,435   
6             12,715                                10,875            10,875   
7             91,819                                84,310            84,310   
8                                                                              
9                                                                              
10            52,075                                48,238            48,238   
11             4,527                                 4,041             4,041   
12            56,602                                52,279            52,279   
13            35,217                                32,031            32,031   
14                                                                             
15                                                                             
16             4,451                                 3,902             3,902   
17             5,197                                 4,783             4,783   
18             9,648                                 8,685             8,685   
19                                                                             
20            25,569                                23,346            23,346   
21               349                                   560               560   
22            25,918                                23,906            23,906   
23             3,682                                 3,941             3,941   
24            22,236                                     $            19,965   
25     

# Using Pandas

In [82]:
sales_data_table = pd.read_html(r"sec-edgar-filings\0000320193\10-Q\0000912057-02-004945\filing-details.html")

In [86]:
sales_data_table[3]

Unnamed: 0_level_0  \
                                   Unnamed: 0_level_1   
0                                           Net sales   
1                                       Cost of sales   
2                                                 NaN   
3                                                 NaN   
4                                                 NaN   
5                                 Operating expenses:   
6                                                 NaN   
7                                                 NaN   
8                                                 NaN   
9                                                 NaN   
10                                                NaN   
11                                                NaN   
12                                     Operating loss   
13              Gains on non-current investments, net   
14          Unrealized loss on convertible securities   
15                     Interest and other income, net   
16                                                NaN   
17                                                NaN   
18                                                NaN   
19  Income (loss) before provision for (benefit fr...   
20          Provision for (benefit from) income taxes   
21                                                NaN   
22             Income (loss) before accounting change   
23  Cumulative effect of accounting change, net of...   
24                                                NaN   
25                                  Net income (loss)   
26                                                NaN   
27  Earnings (loss) per common share before accoun...   
28                                                NaN   
29                                                NaN   
30                  Earnings (loss) per common share:   
31                                                NaN   
32                                                NaN   
33  Shares used in computing earnings (loss) per s...   
34                                                NaN   
35                                                NaN   

                                   Unnamed: 1_level_0  \
                                   Unnamed: 1_level_1   
0                                           Net sales   
1                                       Cost of sales   
2                                                 NaN   
3                                        Gross margin   
4                                                 NaN   
5                                 Operating expenses:   
6                            Research and development   
7                Selling, general, and administrative   
8                                 Restructuring costs   
9                                                 NaN   
10                                                NaN   
11                                                NaN   
12                                     Operating loss   
13              Gains on non-current investments, net   
14          Unrealized loss on convertible securities   
15                     Interest and other income, net   
16                                                NaN   
17               Total interest and other income, net   
18                                                NaN   
19  Income (loss) before provision for (benefit fr...   
20          Provision for (benefit from) income taxes   
21                                                NaN   
22             Income (loss) before accounting change   
23  Cumulative effect of accounting change, net of...   
24                                                NaN   
25                                  Net income (loss)   
26                                                NaN   
27  Earnings (loss) per common share before accoun...   
28                                              Basic   
29                                            Diluted   
30                  Earnings (loss) per comm

In [51]:
sales_data_table = sales_data_table.drop(index=[0,1], columns=[1,3,4,7,8,10,11,12,14,15,16,18,19,21])

In [75]:
sales_data_table.columns = pd.MultiIndex.from_arrays([sales_data_table.iloc[1].values, sales_data_table.iloc[0].values])
sales_data_table = sales_data_table.iloc[2:]
sales_data_table

NaN       July 1, 2017      June 25, 2016  \
                                NaN Three Months Ended Three Months Ended   
4   Net Sales by Operating Segment:                NaN                NaN   
5                          Americas              20376                  $   
6                            Europe              10675               9643   
7                     Greater China               8004               8848   
8                             Japan               3624               3529   
9              Rest of Asia Pacific               2729               2375   
10                  Total net sales              45408                  $   
11                              NaN                NaN                NaN   
12            Net Sales by Product:                NaN                NaN   
13                       iPhone (1)              24846                  $   
14                         iPad (1)               4969               4876   
15                          Mac (1)               5592               5239   
16                     Services (2)               7266               5976   
17            Other Products (1)(3)               2735               2219   
18                  Total net sales              45408                  $   
19                              NaN                NaN                NaN   
20           Unit Sales by Product:                NaN                NaN   
21                           iPhone              41026              40399   
22                             iPad              11424               9950   
23                              Mac               4292               4252   

                                  Change      July 1, 2017     June 25, 2016  \
   Three Months Ended Three Months Ended Nine Months Ended Nine Months Ended   
4                 NaN                NaN               NaN               NaN   
5               17963                 13             73501             66384   
6                9643                 11             41929             39110   
7                8848                (10             34963             39707   
8                3529                  3             13875             12604   
9                2375                 15             12387             10982   
10              42358                  7            176655            168787   
11                NaN                NaN               NaN               NaN   
12                NaN                NaN               NaN               NaN   
13              24048                  3            112473            108540   
14               4876                  2             14391             16373   
15               5239                  7             18680             17092   
16               5976                 22             21479             18023   
17               2219                 23              9632              8759   
18              42358                  7            176655            168787   
19                NaN                NaN               NaN               NaN   
20                NaN                NaN               NaN               NaN   
21              40399                  2            170079            166371   
22               9950                 15             33427             36323   
23               4252                  1             13865             13598   

              Change  
   Nine Months Ended  
4                NaN  
5                 11  
6                  7  
7                (12  
8                 10  
9                 13  
10                 5  
11               NaN  
12               NaN  
13                 4  
14               (12  
15                 9  
16                19  
17                10  
18                 5  
19               NaN  
20               NaN  
21                 2  
22                (8  
23                 2